# Produce Additional Files

##  Imports

In [7]:
import pandas as pd
import numpy as np
import csv
from pathlib import Path
import re
from calendar import month_name

## Annual Cycle Data

The annual cycle data just takes the mean for each month through all the station's precipitation readings. Skip missing values.

How are the percentiles calculated???

- Not normal distributions
- Percentiles doesn't seem to work exactly

I'm starting to think something is wrong with their annual cycles percentile data... For example take [https://climexp.knmi.nl/getprcpall.cgi?id=someone@somewhere&WMO=74604&STATION=VANDENBERG/AFB&extraargs=]. The 97.5th percentile for January is 254.558, but the maximum reading for January at this station is 236.2. By the definition of a percentile, this should be impossible. Every calculator and method I'm using to calculate the percentiles results in numbers that don't match up with the file that's produced. Considering these issues, I'm going to produce my own percentiles.

If I'm going to check again (and don't want to copy it), the data for January is 22.6, 27.4, 28.2, 29, 30, 41.4, 46.7, 48, 51.3, 53.3, 87.1, 131.3, 236.2 (13 members overall, excluding missing values).

In [7]:
testarray = np.array([22.6, 27.4, 28.2, 29, 30, 41.4, 46.7, 48, 51.3, 53.3, 87.1, 131.3, 236.2, np.nan, np.nan, np.nan, np.nan, np.nan, np.nan])
print(np.nanpercentile(testarray, [2.5, 17, 50, 83, 97.5]))

testarray1 = np.array([22.6, 27.4, 28.2, 29, 30, 41.4, 46.7, 48, 51.3, 53.3, 87.1, 131.3, 236.2])
print(np.percentile(testarray1, [2.5, 17, 50, 83, 97.5]))

# will use population standard deviation to show pure data spread without assuming a greater population (default np std function)
print(np.std(testarray1))

# ??? I'm so confused

[ 24.04   28.232  46.7    85.748 204.73 ]
[ 24.04   28.232  46.7    85.748 204.73 ]
57.36100978702329


In [ ]:
# # assumes detailed prcp data file format
# def create_annual_csv(file_path, csv_target_path):
#     print('Creating annual cycle data...')

#     prcp_df = pd.read_csv(file_path)

#     headers = ['Station', 'Month', 'Mean', 'Standard Deviation', '2.5%', '17%', '50%', '50%', '83%', '97.5%']
#     to_csv_lines = []

#     curr_station = ''

#     # go through every row, while station code is the same, add on for each month (unless -999.9)
#     for row in range(prcp_df.shape[0]):
#         if curr_station == prcp_df.iat[row, 0]:
            

#         else:
#             to_csv_lines.append()
            
#             readings_1 = []
#             readings_2 = []
#             readings_3 = []
#             readings_4 = []
#             readings_5 = []
#             readings_6 = []
#             readings_7 = []
#             readings_8 = []
#             readings_9 = []

In [2]:
# assumes detailed prcp data file format
# fix this, currently not detecting -999.9 properly
def create_annual_csv(file_path, csv_target_path):
    print('Creating annual cycle data...')

    prcp_df = pd.read_csv(file_path, converters={'Station': str})
    station_list = pd.unique(prcp_df['Station'])
    all_stations = np.array(prcp_df['Station'].tolist())

    header = ['Station', 'Month', 'Mean', 'Standard Deviation', '2.5%', '17%', '50%', '83%', '97.5%']
    to_csv_lines = []

    # drop unecessary columns
    prcp_df = prcp_df.drop(columns=['Station', 'Identifier', 'Year'])
    prcp_np = prcp_df.to_numpy()
    prcp_np[prcp_np == -999.9] = np.nan         # set all instances of -999.9 to nan

    for station in station_list:

        mask = np.nonzero(all_stations == station)      # get all indices where the station is the same
        station_data = prcp_np[mask, :]
        station_data = np.reshape(station_data, (station_data.shape[1], 12))

        means = np.nanmean(station_data, axis=0)        # stats for each month column
        stds = np.nanstd(station_data, axis=0)
        prctls = np.transpose(np.nanpercentile(station_data, [2.5, 17, 50, 83, 97.5], axis=0))

        stats = np.insert(prctls, 0, stds, axis=1)
        stats = np.insert(stats, 0, means, axis=1)
        # stats = np.insert(stats, 0, station, axis=1)

        if stats.shape[0] != 12:
            print(f'BAD for station {station}')

        # print(means)
        # print(stds)
        # print(prctls)
        # print(stats.shape)

        to_csv_lines.extend(stats.tolist())
        # print(to_csv_lines)

    for station_no in range(len(station_list)):
        for i in range(12):
            line = to_csv_lines[((station_no * 12) + i)]
            line.insert(0, month_name[i + 1])
            line.insert(0, station_list[station_no])     # insert station codes at each line
            to_csv_lines[((station_no * 12) + i)] = line

    with open(csv_target_path, 'w', newline='') as csv_file:
        writer = csv.writer(csv_file)
        writer.writerow(header)
        writer.writerows(to_csv_lines)
    
    print('Done.')

In [3]:
path = '../detailed_prcp_data.csv'
target_path = '../annual_cycles_data.csv'     # include path to file and expected file name here

create_annual_csv(path, target_path)

Creating annual cycle data...


<ipython-input-2-2014153b0209>:23: RuntimeWarning: Mean of empty slice
  means = np.nanmean(station_data, axis=0)        # stats for each month column
c:\Users\Cecile Dai\AppData\Local\Programs\Python\Python38\lib\site-packages\numpy\lib\nanfunctions.py:1879: RuntimeWarning: Degrees of freedom <= 0 for slice.
  var = nanvar(a, axis=axis, dtype=dtype, out=out, ddof=ddof,
c:\Users\Cecile Dai\AppData\Local\Programs\Python\Python38\lib\site-packages\numpy\lib\nanfunctions.py:1584: RuntimeWarning: All-NaN slice encountered
  result = np.apply_along_axis(_nanquantile_1d, axis, a, q,


Done.


In [6]:
file_path = '../detailed_prcp_data.csv'
csv_target_path = '../annual_cycles_data.csv'

In [22]:

print('Creating annual cycle data...')

prcp_df = pd.read_csv(file_path, converters={'Station': str})
station_list = pd.unique(prcp_df['Station'])
all_stations = np.array(prcp_df['Station'].tolist())

header = ['Station', 'Month', 'Mean', 'Standard Deviation', '2.5%', '17%', '50%', '83%', '97.5%']
to_csv_lines = []

# drop unecessary columns
prcp_df = prcp_df.drop(columns=['Station', 'Identifier', 'Year'])
prcp_np = prcp_df.to_numpy()
prcp_np[prcp_np == -999.9] = np.nan         # set all instances of -999.9 to nan

for station in station_list:

    mask = np.nonzero(all_stations == station)      # get all indices where the station is the same
    station_data = prcp_np[mask, :]
    station_data = np.reshape(station_data, (station_data.shape[1], 12))

    means = np.nanmean(station_data, axis=0)        # stats for each month column
    stds = np.nanstd(station_data, axis=0)
    prctls = np.transpose(np.nanpercentile(station_data, [2.5, 17, 50, 83, 97.5], axis=0))

    stats = np.insert(prctls, 0, stds, axis=1)
    stats = np.insert(stats, 0, means, axis=1)
    # stats = np.insert(stats, 0, station, axis=1)

    if stats.shape[0] != 12:
        print(f'BAD for station {station}')

    # print(means)
    # print(stds)
    # print(prctls)
    # print(stats.shape)

    to_csv_lines.extend(stats.tolist())
    # print(to_csv_lines)

Creating annual cycle data...


<ipython-input-22-7b13021e3844>:21: RuntimeWarning: Mean of empty slice
  means = np.nanmean(station_data, axis=0)        # stats for each month column
c:\Users\Cecile Dai\AppData\Local\Programs\Python\Python38\lib\site-packages\numpy\lib\nanfunctions.py:1879: RuntimeWarning: Degrees of freedom <= 0 for slice.
  var = nanvar(a, axis=axis, dtype=dtype, out=out, ddof=ddof,
c:\Users\Cecile Dai\AppData\Local\Programs\Python\Python38\lib\site-packages\numpy\lib\nanfunctions.py:1584: RuntimeWarning: All-NaN slice encountered
  result = np.apply_along_axis(_nanquantile_1d, axis, a, q,


In [ ]:
print(to_csv_lines)

In [23]:
for station_no in range(len(station_list)):
    for i in range(12):
        print(f'on {((station_no * 12) + i)}')
        line = to_csv_lines[((station_no * 12) + i)]
        # print(line)
        line.insert(0, month_name[i + 1])
        line.insert(0, station_list[station_no])     # insert station codes at each line
        # print(line)
        to_csv_lines[((station_no * 12) + i)] = line

on 0
on 1
on 2
on 3
on 4
on 5
on 6
on 7
on 8
on 9
on 10
on 11
on 12
on 13
on 14
on 15
on 16
on 17
on 18
on 19
on 20
on 21
on 22
on 23
on 24
on 25
on 26
on 27
on 28
on 29
on 30
on 31
on 32
on 33
on 34
on 35
on 36
on 37
on 38
on 39
on 40
on 41
on 42
on 43
on 44
on 45
on 46
on 47
on 48
on 49
on 50
on 51
on 52
on 53
on 54
on 55
on 56
on 57
on 58
on 59
on 60
on 61
on 62
on 63
on 64
on 65
on 66
on 67
on 68
on 69
on 70
on 71
on 72
on 73
on 74
on 75
on 76
on 77
on 78
on 79
on 80
on 81
on 82
on 83
on 84
on 85
on 86
on 87
on 88
on 89
on 90
on 91
on 92
on 93
on 94
on 95
on 96
on 97
on 98
on 99
on 100
on 101
on 102
on 103
on 104
on 105
on 106
on 107
on 108
on 109
on 110
on 111
on 112
on 113
on 114
on 115
on 116
on 117
on 118
on 119
on 120
on 121
on 122
on 123
on 124
on 125
on 126
on 127
on 128
on 129
on 130
on 131
on 132
on 133
on 134
on 135
on 136
on 137
on 138
on 139
on 140
on 141
on 142
on 143
on 144
on 145
on 146
on 147
on 148
on 149
on 150
on 151
on 152
on 153
on 154
on 155
on 156
on 157
on 1

In [24]:
with open(csv_target_path, 'w', newline='') as csv_file:
    writer = csv.writer(csv_file)
    writer.writerow(header)
    writer.writerows(to_csv_lines)

print('Done.')

Done.


In [ ]:
test_df = pd.read_csv('../detailed_prcp_data.csv', converters={'Station': str})
testy = test_df.loc[test_df['Station'] == '60354.1']
print(testy)

In [93]:
jans = []
for row in range(testy.shape[0]):
    jan = testy.iat[row, 3]
    if jan != -999.9:
        jans.append(jan)
print(jans)

[85.0, 93.0, 122.0, 157.0, 189.0, 90.0, 166.0, 200.0, 71.0, 107.0, 297.0, 39.0, 136.0, 156.0, 77.0, 61.0, 181.0, 29.0, 28.0, 236.0, 111.0, 223.0, 13.0, 200.0, 95.0, 43.0, 49.0, 124.0, 73.0, 78.0, 93.0, 113.0, 60.0, 189.0, 51.0, 6.0, 54.0, 8.0, 122.0, 32.0, 98.0, 40.0, 68.0, 124.0, 20.0, 102.0, 59.0, 68.0, 140.0, 95.0, 91.0, 170.0, 87.0, 123.0, 112.0, 113.0, 96.0, 109.0, 80.0, 52.0, 56.0, 18.0, 46.0, 77.0, 14.0, 19.0, 210.0, 104.0, 103.0, 59.0, 116.0, 113.0, 83.0, 121.0, 116.0, 30.0, 150.0, 205.0, 66.0, 112.0, 33.0, 161.0, 32.0, 42.0, 67.0, 240.0, 87.0, 5.0, 8.0, 91.0, 113.0, 106.0, 70.0, 165.0, 85.0, 113.0, 157.0, 140.0, 25.0, 17.0, 49.0, 43.0, 116.0, 36.0, 112.0, 35.0, 10.0, 197.0, 247.0, 100.0, 116.0, 110.0, 114.0, 88.0, 200.0, 146.0, 215.0, 109.0, 87.0, 131.0, 140.0, 35.0, 121.0, 170.0, 110.0, 110.0, 40.0, 138.0, 42.0, 50.0, 20.0, 61.0, 45.0, 129.0, 122.0, 161.0, 15.0, 33.0, 89.0, 58.0, 106.0, 58.0, 87.0, 40.0, 149.0, 4.0, 118.0, 103.0, 92.0, 44.0, 43.0, 146.0, 54.0, 155.0, 18.0]


In [94]:
print(np.mean(jans))
print(np.std(jans))
print(np.percentile(jans, [2.5, 17, 50, 83, 97.5]))

95.78064516129032
57.92957581773301
[  8.    39.18  93.   148.46 224.95]


In [101]:
print(np.nanmean([np.nan, np.nan, np.nan]))

nan


<ipython-input-101-ee33fc1f5a12>:1: RuntimeWarning: Mean of empty slice
  print(np.nanmean([np.nan, np.nan, np.nan]))


## Anomaly Data

Anomaly for a certain month and year is monthly reading - monthly average (from the annual cycle data).

In [11]:
# assumes detailed prcp data file format
def create_anomaly_csv(prcp_file_path, annual_file_path, csv_target_path):
    print('Creating anomaly data...')

    prcp_df = pd.read_csv(prcp_file_path, converters={'Station': str})
    annual_cycle_df = pd.read_csv(annual_file_path, converters={'Station' : str})

    station_list = pd.unique(prcp_df['Station'])
    year_list = np.array(prcp_df['Year'].tolist())
    all_stations = np.array(prcp_df['Station'].tolist())

    header = ['Station', 'Year', 'January', 'February', 'March', 'April', 'May', 'June', 'July', 'August', 'September', 'October', 'November', 'December']
    to_csv_lines = []

    # drop unecessary columns
    prcp_df = prcp_df.drop(columns=['Station', 'Identifier', 'Year'])
    prcp_np = prcp_df.to_numpy()
    prcp_np[prcp_np == -999.9] = np.nan         # set all instances of -999.9 to nan

    monthly_means = np.array(annual_cycle_df['Mean'].tolist())

    # print(monthly_means)

    current_station = ''
    station_index = -1       # station number of unique station list

    # weird_stations = []

    # weird_index = -1

    for row in range(prcp_np.shape[0]):
        # the order of the stations in both files are the same - take advantage of this

        # get annual monthly means only every time the station changes
        if not all_stations[row].__eq__(current_station):
            # print(f'{current_station} and {all_stations[row]}')
            current_station = all_stations[row]
            # weird_index += 1
            # weird_stations.append(current_station)
            station_index += 1 if station_index < len(station_list) - 1 else 0
            station_monthly_means = monthly_means[(station_index * 12) : ((station_index + 1) * 12)]
            # print(f'{station_index}/{len(station_list)} on row {row} and full station index {station_index * 12}')
            # print(weird_index)
            # print(station_monthly_means)

        anoms = prcp_np[row] - station_monthly_means
        
        if not np.isnan(anoms).all():
            # anoms[anoms == np.nan] = -999.9
            anoms = np.nan_to_num(anoms, nan=-999.9)
            anoms = anoms.tolist()
            anoms.insert(0, year_list[row])
            anoms.insert(0, current_station)
            to_csv_lines.append(anoms)
        
        # print(f'row {row}/{prcp_np.shape[0]}')

    with open(csv_target_path, 'w', newline='') as csv_file:
        writer = csv.writer(csv_file)
        writer.writerow(header)
        writer.writerows(to_csv_lines)

    # return weird_stations
    
    print('Done.')

In [12]:
prcp_path = '../detailed_prcp_data.csv'
ann_path = '../annual_cycles_data.csv'     # include path to file and expected file name here
target_path = '../anomaly_data.csv'

weird = create_anomaly_csv(prcp_path, ann_path, target_path)

Creating anomaly data...
Done.


In [46]:
print(len(weird))

20591


In [ ]:
# found the problem. See identifier 4057876210011972. it should be 78762.100, but its recognized as 78762
# fix the precipitation file

In [62]:
ann_df = pd.read_csv('../annual_cycles_data.csv', converters={'Station': str})
p_df = pd.read_csv('../detailed_prcp_data.csv', converters={'Station': str})

In [63]:
p_station_list = pd.unique(p_df['Station'])
ann_station_list = pd.unique(ann_df['Station'])

In [70]:
dd = '4057876210011972'
print(dd[3:8])
print(dd[8:11])

78762
100


In [67]:
print(p_station_list[0:2])
print(ann_station_list[0:2])

['60354.1' '60355']
['60354.1' '60355']


In [57]:
for p in range(len(p_station_list)):
    if p_station_list[p] != ann_station_list[p]:
        print(f'flag at {p} for p station {p_station_list[p]} and a station {ann_station_list[p]}')

In [58]:
u_p = np.unique(p_station_list)

In [59]:
for p in range(len(p_station_list)):
    if p_station_list[p] != u_p[p]:
        print(f'flag at {p} for p station {p_station_list[p]} and a station {u_p[p]}')

flag at 0 for p station 60354.1 and a station 01001
flag at 1 for p station 60355 and a station 01005
flag at 2 for p station 60360 and a station 01008
flag at 3 for p station 60390 and a station 01025
flag at 4 for p station 60395.2 and a station 01025.2
flag at 5 for p station 60400 and a station 01028
flag at 6 for p station 60402 and a station 01032
flag at 7 for p station 60403 and a station 01055.2
flag at 8 for p station 60403.1 and a station 01062.1
flag at 9 for p station 60419 and a station 01065
flag at 10 for p station 60425 and a station 01074.2
flag at 11 for p station 60425.2 and a station 01089.1
flag at 12 for p station 60430 and a station 01092
flag at 13 for p station 60444 and a station 01098
flag at 14 for p station 60445 and a station 01121.1
flag at 15 for p station 60457.1 and a station 01137.1
flag at 16 for p station 60468 and a station 01137.2
flag at 17 for p station 60475 and a station 01137.3
flag at 18 for p station 60490 and a station 01152
flag at 19 fo

In [51]:
print(len(p_station_list))
print(len(ann_station_list))

20549
20549


In [48]:
p_list = (p_station_list.tolist()).extend([''] * (len(weird) - len(p_station_list)))

In [49]:
equal = p_station_list == weird
print(len(equal))
print(equal.tolist().count(True))

TypeError: object of type 'bool' has no len()

In [60]:
for i in range(len(p_station_list)):
    if p_station_list[i] != weird[i]:
        print(f'flag at {i} for p station {p_station_list[i]} and weird station {weird[i]}')
        print(f'previously p station {p_station_list[i - 1]} and weird station {weird[i - 1]}')

flag at 12114 for p station 78762.1 and weird station 78762
previously p station 78762.99 and weird station 78762.99
flag at 12115 for p station 78767 and weird station 78762.1
previously p station 78762.1 and weird station 78762
flag at 12116 for p station 78767.1 and weird station 78762.2
previously p station 78767 and weird station 78762.1
flag at 12117 for p station 78767.2 and weird station 78762.3
previously p station 78767.1 and weird station 78762.2
flag at 12118 for p station 78767.3 and weird station 78762.4
previously p station 78767.2 and weird station 78762.3
flag at 12119 for p station 78767.4 and weird station 78762.5
previously p station 78767.3 and weird station 78762.4
flag at 12120 for p station 78767.5 and weird station 78762.6
previously p station 78767.4 and weird station 78762.5
flag at 12121 for p station 78767.6 and weird station 78762.7
previously p station 78767.5 and weird station 78762.6
flag at 12122 for p station 78767.7 and weird station 78762.8
previous

# Percentage Anomalies

Oh god I think I'm going to need to make an entirely new csv files just for percentage anomalies. No clean way to stick them in anomalies!

In [15]:
anom_data = pd.read_csv('../for_database/anomaly_data.csv', converters={'station': str})
cycles_data = pd.read_csv('../for_database/annual_cycles_data.csv', converters={'station': str})

In [16]:
station_list = pd.unique(anom_data['station'])
year_list = np.array(anom_data['year'].tolist())
all_stations = np.array(anom_data['station'].tolist())

header = ['station', 'year', 'january', 'february', 'march', 'april', 'may', 'june', 'july', 'august', 'september', 'october', 'november', 'december']
to_csv_lines = []

# drop unecessary columns
anom_df = anom_data.drop(columns=['station', 'year'])
anom_np = anom_df.to_numpy()

monthly_means = np.array(cycles_data['mean'].tolist())

current_station = ''
station_index = -1       # station number of unique station list

for row in range(anom_np.shape[0]):
    # the order of the stations in both files are the same - take advantage of this

    # get annual monthly means only every time the station changes
    if not all_stations[row].__eq__(current_station):
        current_station = all_stations[row]
        station_index += 1 if station_index < len(station_list) - 1 else 0    # stop incrementing if you reach the end of the list
        station_monthly_means = monthly_means[(station_index * 12) : ((station_index + 1) * 12)]

    anoms_pcnt = (anom_np[row]/station_monthly_means) * 100   # get percentage anomaly

    # dividing by 0 will result in inf - keep as this for now
    
    if not np.isnan(anoms_pcnt).all():
        anoms_pcnt = anoms_pcnt.tolist()
        anoms_pcnt.insert(0, year_list[row])
        anoms_pcnt.insert(0, current_station)
        to_csv_lines.append(anoms_pcnt)

with open('../for_database/anomaly_percentage_data.csv', 'w', newline='') as csv_file:
    writer = csv.writer(csv_file)
    writer.writerow(header)
    writer.writerows(to_csv_lines)

print('Done.')

C:\Users\Cecile Dai\AppData\Local\Temp\ipykernel_3496\1388568858.py:26: RuntimeWarning: invalid value encountered in divide
  anoms_pcnt = (anom_np[row]/station_monthly_means) * 100   # get percentage anomaly


Done.
